## BoF com 1 dicionário homogênio + LPB com 8 vizinhos

In [ ]:
import numpy as np
import cv2
from matplotlib import pyplot as plt
from sklearn.cluster import KMeans
import os
from sklearn import metrics

PATH_MELANOMA = '../DermMel/test/Melanoma'
PATH_NOTMELANOMA = '../DermMel/test/NotMelanoma'
PATH_GENERATE_DIC = '../DermMel/geracao_dicionario/melanomas'

files_path_dic = os.listdir(PATH_GENERATE_DIC) 
files_path_dic = [PATH_GENERATE_DIC + '/' + path for path in files_path_dic]

dic_des = []
palavras = []
array_desc = []

for path_img in files_path_dic:
#     img = cv2.imread(path_img)
#     plt.imshow(img[:,:,::-1])
    # plt.show()

    img = cv2.imread(path_img,0) # Leitura da imagem com filtro em escada de cinza
    plt.gray()
    plt.imshow(img)
    plt.show()

    sift = cv2.xfeatures2d.SIFT_create()

    # Encontrando os pontos-de-interesse
    kp = sift.detect(img,None)

    # computando o vetor-de-característica para cada ponto detectado
    kp, des = sift.compute(img, kp)
                    
    dic_des.extend(des)       

# print(dic_des)
# Print da imagem com regiões de interesse destacadas
# img2 = cv2.drawKeypoints(img, kp, None)
# plt.imshow(img2),plt.show()


# Clusterização por meio de Kmeans
K = 40

kmeans_model = KMeans(n_clusters=K).fit(dic_des) #dic_des são os vetores-de-características concatenados

# criando o dicionário de palavras
palavras = np.array(kmeans_model.cluster_centers_)

In [7]:
'''
Método de extração de arquivo .arff. Autor: Glauco Vitor.
'''

def gravar_arquivo_arff(base_teste, classes): # 0 para NAO_MELANOMA e 1 para MELANOMA
    tam = len(base_teste[0][0])
    file = open('dic1_lbp8_sift_k40.arff','w') 
 
    file.write('@relation cancer\n') 
    for i in range(tam):
        file.write('@attribute '+ str(i) +' NUMERIC\n') 
    
    file.write('@attribute classes {')
    
    a = set(classes)
    
    for i in a:
        file.write(str(i)+',')
    
    file.write('}')    
    
    for i in range(tam):
         len(set(classes))
    
    file.write('\n@data\n') 

    for item in base_teste:
        for i in range(len(item[0])):
            file.write("%s," % str(item[0][i])) 
        file.write("%s\n" % item[1])    
 
    file.close() 
    print('arquivo gravado')


In [8]:
'''
Distância euclidiana para a atribuição dos centróides a cada elemento da imagem.
'''

def distancia(a, b):
    M = len(a)
    soma = 0
    for i in range(M):
        soma = soma + ((a[i]-b[i])**2)
    return np.sqrt(soma)


In [9]:
from skimage import feature
import numpy as np
 
'''
Descritor LBP
'''
    

def extrair_caracteristica_lbp(image):
    # compute the Local Binary Pattern representation
    # of the image, and then use the LBP representation
    # to build the histogram of patterns
    
    numPoints = 8
    radius = 1
    eps=1e-7
    
    lbp = feature.local_binary_pattern(image, numPoints, radius, method="default")
    (hist, _) = np.histogram(lbp.ravel(),
        bins = np.arange(0, 257),
        range = (0, numPoints + 2))
    
#     (hist, _) = np.histogram(lbp.ravel(),
#         bins = np.arange(0, numPoints + 3),
#         range = (0, numPoints + 2))
    

    # normalize the histogram
    hist = hist.astype("float")
    hist /= (hist.sum() + eps)
    
    # return the histogram of Local Binary Patterns
    return hist  # hist.lenght = K + 2

In [13]:
'''
Descritor SIFT
Método de extração para todas as imagens da base de treinamento. 
O vetor de descrição tomado por base é o que foi gerado no início.
'''

def extrair_caracteristica_sift(img):
    sift = cv2.xfeatures2d.SIFT_create()
    # encontrando os pontos-de-interesse
    kp = sift.detect(img,None)
#     print('Qtde Pontos Detectados: ', len(kp))
    
    kp, des = sift.compute(img, kp)
    pontos_rotulados = []

    for ponto in des:
        min = 9999
        label = -1
        for i in range(len(array_desc)): #Tem o dobro do tamanho agora.
            dist = distancia(ponto, array_desc[i])
            if(dist < min):
                min = dist
                label = i
        pontos_rotulados.append(label)
    
#     hist = np.zeros(K)
    hist = np.zeros(K) # Tenho 6 cluster para um K=3, pois são 2 dicionários.   
    
#     print("historico zeros")
#     print(hist)
    
#     print("Pontos rotulados")
#     print(pontos_rotulados)

    for i in pontos_rotulados:
        hist[i] += 1
    
#     print(hist)
    return hist # Frequência em que cada palavra centroide aparece

In [14]:
def extrair_caracteristica(imagem):
    hist = []
    hist_lbp = extrair_caracteristica_lbp(imagem)
    hist_sift = extrair_caracteristica_sift(imagem)
    
    hist.extend(hist_lbp)
    hist.extend(hist_sift)
    
    print("hist_lbp size:")
    print(len(hist_lbp))
    print("Hist_sift size:")
    print(len(hist_sift))
    print("Histograma completo size:")
    print(len(hist))
    print("Histograma concatenado: ")
    print(hist)
    print("-------------------------------------------------------------------------------------------------")
    
    return hist
    

In [15]:
import cv2 as cv2
import numpy as np
import matplotlib.pyplot as plt
import os
from sklearn.cluster import KMeans
from sklearn import metrics

files_path_nao_melanoma = os.listdir(PATH_NOTMELANOMA) 
files_path_nao_melanoma = [PATH_NOTMELANOMA+'/'+path for path in files_path_nao_melanoma]
files_path_melanoma = os.listdir(PATH_MELANOMA)
files_path_melanoma = [PATH_MELANOMA+'/'+path for path in files_path_melanoma]


all_image_paths = [files_path_nao_melanoma, files_path_melanoma]

base = []
classes = []

#extraindo as características das imagens na base de dados
for i in range(len(all_image_paths)):
    for img_path in all_image_paths[i][:500]:
        imagem = cv2.imread(img_path, 0)
        caracteristica = extrair_caracteristica(imagem)
        classes.append(i)
        base.append((caracteristica, i))
    print('Classe final: '+str(i))
    print('Size')
    print(len(caracteristica))

gravar_arquivo_arff(base, classes)

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.04960370370368533, 0.014851851851846351, 0.001303703703703221, 0.006896296296293742, 0.020892592592584854, 0.004274074074072491, 0.006833333333330803, 0.01934444444443728, 0.001148148148147723, 0.0002814814814813772, 6.666666666664198e-05, 0.00020740740740733058, 0.007044444444441835, 0.001170370370369937, 0.006011111111108885, 0.0133407407407358, 0.015196296296290669, 0.004125925925924398, 0.00037777777777763785, 0.001474074074073528, 0.0042999999999984075, 0.0006592592592590151, 0.0011777777777773415, 0.0025518518518509066, 0.006455555555553164, 0.001629629629629026, 0.0002185185185184376, 0.0010222222222218437, 0.01896296296295594, 0.0025296296296286928, 0.01343703703703206, 0.018862962962955976, 0.0011925925925921508, 0.00034074074074061454, 2.9629629629618656e-05, 0.00015555555555549794, 0.0005370370370368381, 9.999999999996297e-05, 0.00017037037037030727, 0.0003518518518517215, 5.18518

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.03897037037035594, 0.015785185185179337, 0.0011925925925921508, 0.007099999999997371, 0.012851851851847092, 0.00385925925925783, 0.006659259259256793, 0.023118518518509955, 0.001374074074073565, 0.0004740740740738985, 5.925925925923731e-05, 0.0001518518518517956, 0.0074333333333305805, 0.001707407407406775, 0.007929629629626693, 0.021466666666658717, 0.016237037037031023, 0.003918518518517067, 0.0003481481481480192, 0.0012999999999995186, 0.0029185185185174375, 0.0004925925925924102, 0.0011888888888884484, 0.00258888888888793, 0.007862962962960051, 0.0014851851851846352, 0.00016296296296290262, 0.0005592592592590522, 0.021462962962955013, 0.0029037037037026284, 0.01819999999999326, 0.02495555555554631, 0.0011851851851847463, 0.0003592592592591262, 4.444444444442798e-05, 0.00020370370370362826, 0.0003111111111109959, 0.00010370370370366529, 0.00013703703703698628, 0.00034074074074061454, 7.40

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.042466666666650936, 0.01718148148147512, 0.0010407407407403552, 0.0049925925925907435, 0.014237037037031764, 0.005274074074072121, 0.005203703703701776, 0.021733333333325285, 0.0014666666666661235, 0.00044444444444427983, 4.444444444442798e-05, 0.00014814814814809329, 0.00573333333333121, 0.0019037037037029987, 0.006037037037034801, 0.01956296296295572, 0.017796296296289704, 0.0058481481481459825, 0.0003592592592591262, 0.0013629629629624582, 0.00341481481481355, 0.000925925925925583, 0.0010629629629625693, 0.0037444444444430574, 0.005418518518516512, 0.0014370370370365049, 0.00014444444444439096, 0.00047037037037019617, 0.018718518518511584, 0.003837037037035616, 0.01456296296295757, 0.02987407407406301, 0.0009629629629626063, 0.0003740740740739355, 3.333333333332099e-05, 0.00010740740740736763, 0.0003333333333332099, 9.25925925925583e-05, 0.00011851851851847462, 0.00044814814814798216, 4.4

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.0821185185184881, 0.01753703703703054, 0.0022777777777769344, 0.007292592592589892, 0.02664814814813828, 0.00474814814814639, 0.008074074074071083, 0.014074074074068861, 0.002440740740739837, 0.0006555555555553127, 0.00014814814814809329, 0.0005222222222220288, 0.00800370370370074, 0.001674074074073454, 0.004999999999998148, 0.009499999999996482, 0.017496296296289817, 0.0036629629629616064, 0.0006444444444442057, 0.001629629629629026, 0.004655555555553832, 0.0007333333333330617, 0.0015925925925920027, 0.0020333333333325803, 0.006881481481478933, 0.0017814814814808217, 0.0004518518518516845, 0.0013666666666661605, 0.013144444444439575, 0.0022037037037028876, 0.0093703703703669, 0.011970370370365937, 0.0021037037037029247, 0.0006111111111108847, 7.03703703703443e-05, 0.0003370370370369122, 0.001037037037036653, 0.0001851851851851166, 0.0004592592592590892, 0.0007777777777774897, 0.000118518518

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.04394444444442817, 0.01671111111110492, 0.0010740740740736762, 0.005307407407405442, 0.015907407407401517, 0.003659259259257904, 0.0051592592592573485, 0.018225925925919175, 0.0009666666666663087, 0.00037777777777763785, 2.222222222221399e-05, 0.00014444444444439096, 0.004814814814813032, 0.0010925925925921879, 0.004999999999998148, 0.01165925925925494, 0.01661481481480866, 0.0058185185185163635, 0.00039999999999985186, 0.0012740740740736021, 0.004807407407405627, 0.000803703703703406, 0.0015444444444438724, 0.0038074074074059975, 0.0047962962962945195, 0.0012666666666661976, 0.00015925925925920026, 0.00044814814814798216, 0.022529629629621285, 0.003714814814813439, 0.016333333333327284, 0.02841481481480429, 0.0011740740740736391, 0.0004925925925924102, 5.925925925923731e-05, 0.0001518518518517956, 0.0003518518518517215, 5.1851851851832646e-05, 0.00013333333333328395, 0.0004259259259257682, 

...

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.02044802295914292, 0.011260363520385721, 0.00033880739795850843, 0.004085618622440837, 0.013073979591810678, 0.0016741071428538065, 0.005102040816316362, 0.025868941326479055, 0.0003587372448972442, 0.00011957908163241474, 0.0, 5.978954081620737e-05, 0.004504145408154288, 0.0005978954081620737, 0.005102040816316362, 0.01897321428567647, 0.012157206632628832, 0.004384566326521874, 0.0001793686224486221, 0.0008171237244881674, 0.0013950892857115052, 0.00011957908163241474, 0.0004982461734683947, 0.0022321428571384083, 0.004364636479583138, 0.000856983418365639, 7.971938775494316e-05, 0.00021922831632609368, 0.032266422193813246, 0.0024314413265257664, 0.02202248086730305, 0.03852439413257628, 0.00047831632652965895, 0.0001793686224486221, 0.0, 0.00011957908163241474, 0.00027901785714230104, 0.0, 3.985969387747158e-05, 0.0003985969387747158, 0.0, 0.0, 0.0, 0.0, 5.978954081620737e-05, 0.0, 9.964

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.056955555555534464, 0.018351851851845055, 0.0021148148148140314, 0.008125925925922916, 0.014218518518513253, 0.004348148148146538, 0.007944444444441503, 0.02304444444443591, 0.002288888888888041, 0.0006592592592590151, 0.00011851851851847462, 0.0003703703703702332, 0.008214814814811773, 0.0019592592592585336, 0.008918518518515215, 0.023792592592583782, 0.01885185185184487, 0.0038333333333319137, 0.0005518518518516475, 0.001474074074073528, 0.0035851851851838572, 0.0005740740740738615, 0.001729629629628989, 0.002866666666665605, 0.007892592592589669, 0.00154074074074017, 0.00044814814814798216, 0.0008555555555552387, 0.01909259259258552, 0.0027629629629619397, 0.01894444444443743, 0.025592592592583115, 0.001929629629628915, 0.0005518518518516475, 9.629629629626063e-05, 0.00020740740740733058, 0.0004555555555553868, 0.00017777777777771192, 0.0002814814814813772, 0.00047037037037019617, 0.00014

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.02818888888887845, 0.012614814814810143, 0.0007777777777774897, 0.006092592592590336, 0.010562962962959051, 0.0024962962962953718, 0.006159259259256978, 0.0270037037036937, 0.0009222222222218806, 0.00032222222222210285, 5.1851851851832646e-05, 0.0001740740740740096, 0.006837037037034505, 0.0012888888888884114, 0.011129629629625508, 0.033966666666654086, 0.012551851851847203, 0.0032740740740728616, 0.00028518518518507954, 0.0010185185185181413, 0.0021666666666658643, 0.0003111111111109959, 0.0009185185185181784, 0.0022777777777769344, 0.006855555555553016, 0.001114814814814402, 0.00018888888888881893, 0.0004999999999998148, 0.025707407407397884, 0.002374074074073195, 0.031507407407395736, 0.038777777777763416, 0.0007999999999997037, 0.00027407407407397256, 2.9629629629618656e-05, 0.00014814814814809329, 0.00020370370370362826, 4.814814814813031e-05, 9.999999999996297e-05, 0.000355555555555423

hist_lbp size:
256
Hist_sift size:
40
Histograma completo size:
296
Histograma concatenado: 
[0.03310347576524015, 0.0110809948979371, 0.0007772640306106958, 0.006656568877537754, 0.02002949617342947, 0.001992984693873579, 0.006776147959170168, 0.027762276785658957, 0.0008968431122431106, 0.0001992984693873579, 3.985969387747158e-05, 5.978954081620737e-05, 0.008270886479575353, 0.00075733418367196, 0.008211096938759146, 0.020627391581591544, 0.011160714285692042, 0.0024513711734645022, 0.00015943877550988632, 0.0011160714285692042, 0.0017538265306087494, 0.00021922831632609368, 0.0005978954081620737, 0.0013352997448952979, 0.006955516581618791, 0.0010562818877529968, 0.00013950892857115052, 0.0006178252551008095, 0.0240553252550541, 0.0013352997448952979, 0.01845503826526934, 0.02206234056118052, 0.0009566326530593179, 0.00027901785714230104, 1.992984693873579e-05, 0.00011957908163241474, 0.00043845663265218736, 9.964923469367895e-05, 0.00013950892857115052, 0.0006377551020395453, 9.96

arquivo gravado
